In [66]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.feature_selection import SequentialFeatureSelector
from sklearn.linear_model import LinearRegression
from sklearn.metrics import root_mean_squared_error

In [67]:
path = "http://www.iam.fmph.uniba.sk/ospm/Rosa/PDV/01_nhanes-weight.xls"
#path = "01_nhanes-weight.xls"
data = pd.ExcelFile(path).parse('Sheet1')
data["Age"] = data["Age"]/12
data = data.dropna()

data

Gender        Age  Weight  Height  Leg_Length  Arm_Length  Arm_circum  \
0          0  20.083333    64.7     163        34.2        36.2        29.0   
1          0  20.083333    54.0     153        37.2        34.0        26.1   
2          1  20.083333    61.4     165        37.7        35.0        31.4   
3          0  20.083333    74.0     171        37.9        36.2        29.8   
4          0  20.083333    63.6     159        38.1        34.0        29.2   
...      ...        ...     ...     ...         ...         ...         ...   
4974       1  79.833333    89.5     184        43.0        42.8        32.2   
4975       0  79.916667    78.6     151        35.6        34.2        33.5   
4976       1  79.916667    86.5     175        38.6        41.5        32.8   
4977       0  79.916667    58.0     163        40.2        37.5        26.2   
4978       1  79.916667    76.2     168        40.8        39.5        29.8   

      Waist  
0      89.6  
1      85.5  
2      70.1  
3      91.1  
4      74.3  
...     ...  
4974  112.8  
4975  114.9  
4976  100.2  
4977   82.8  
4978  103.5  

[4978 rows x 8 columns]

In [68]:
# X, y a train-test split
y = data["Weight"]
X = data.copy(deep=True)
X.drop(labels="Weight",axis=1,inplace=True)

X_train, X_test, ytrain, ytest = train_test_split(X, y, test_size=0.3, random_state=0)

In [69]:
# "Plny" model
lm_full = LinearRegression()
lm_full.fit(X_train, ytrain)

# moze zahrnat aj napr. kvadraticke vplyvy, interakcie, ...

LinearRegression()

In [70]:
# Selekcia premennych: Forward selection
lm = LinearRegression()
sfs = SequentialFeatureSelector(lm, n_features_to_select=3,
                                direction="forward",
                                scoring="neg_root_mean_squared_error", cv=10) # prave 3 premenne
sfs.fit(X_train, ytrain)

# vybrane premenne
sfs.get_feature_names_out()

array(['Height', 'Arm_circum', 'Waist'], dtype=object)

In [71]:
# Automaticky vyber poctu
lm = LinearRegression()
sfs = SequentialFeatureSelector(lm, n_features_to_select="auto", tol=0,
                                direction="forward",
                                scoring="neg_root_mean_squared_error", cv=10)
sfs.fit(X_train, ytrain)

# vybrane premenne
sfs.get_feature_names_out() # vsetky okrem Arm_Length

array(['Gender', 'Age', 'Height', 'Leg_Length', 'Arm_circum', 'Waist'],
      dtype=object)

In [72]:
# Fit na vybranych premennych

# Vyselektovane premenne
X_train_sel = sfs.transform(X_train)
X_test_sel = sfs.transform(X_test)

lm_sel = LinearRegression()
lm_sel.fit(X_train_sel, ytrain)

LinearRegression()

In [73]:
# Porovnanie na testovacej (~validacnej)
y_pred_full = lm_full.predict(X_test)
y_pred_sel = lm_sel.predict(X_test_sel)

# RMSE
RMSE_full = root_mean_squared_error(ytest, y_pred_full)
RMSE_sel = root_mean_squared_error(ytest, y_pred_sel)

print(f"RMSE full model: {RMSE_full:.4f}, RMSE submodel: {RMSE_sel:.4f}")

RMSE full model: 4.7855, RMSE submodel: 4.7735


In [ ]:
# Dobrovolna DU: Vyskusajte selekciu premennych na predikovanie pohlavia pomocou logistickej regresie